<a href="https://colab.research.google.com/github/GlobalCapybara/cls_161_F2023-GH/blob/main/PrgrmHist_Spcy.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

https://programminghistorian.org/en/lessons/corpus-analysis-with-spacy

In [1]:
# Install and import spaCy
import spacy

# Load spaCy visualizer
from spacy import displacy

# Import os to upload documents and metadata
import os

# Import pandas DataFrame packages
import pandas as pd

# Import graphing package
import plotly.graph_objects as go
import plotly.express as px

# Import drive and files to facilitate file uploads
from google.colab import files

In [2]:
uploaded_files = files.upload()

Saving ENG.G0.35.1.txt to ENG.G0.35.1.txt
Saving ENG.G0.35.2.txt to ENG.G0.35.2.txt
Saving ENG.G0.36.1.txt to ENG.G0.36.1.txt
Saving ENG.G0.37.1.txt to ENG.G0.37.1.txt
Saving ENG.G0.38.1.txt to ENG.G0.38.1.txt
Saving ENG.G0.38.2.txt to ENG.G0.38.2.txt
Saving ENG.G0.38.3.txt to ENG.G0.38.3.txt
Saving ENG.G0.39.2.txt to ENG.G0.39.2.txt
Saving ENG.G0.40.1.txt to ENG.G0.40.1.txt
Saving ENG.G0.41.1.txt to ENG.G0.41.1.txt
Saving ENG.G0.41.2.txt to ENG.G0.41.2.txt
Saving ENG.G0.41.3.txt to ENG.G0.41.3.txt
Saving ENG.G0.42.1.txt to ENG.G0.42.1.txt
Saving ENG.G0.42.2.txt to ENG.G0.42.2.txt
Saving ENG.G0.43.1.txt to ENG.G0.43.1.txt
Saving ENG.G0.43.2.txt to ENG.G0.43.2.txt
Saving ENG.G0.44.1.txt to ENG.G0.44.1.txt
Saving ENG.G0.45.1.txt to ENG.G0.45.1.txt
Saving ENG.G0.46.1.txt to ENG.G0.46.1.txt
Saving ENG.G0.47.1.txt to ENG.G0.47.1.txt
Saving ENG.G0.48.1.txt to ENG.G0.48.1.txt
Saving ENG.G0.49.1.txt to ENG.G0.49.1.txt
Saving ENG.G0.49.2.txt to ENG.G0.49.2.txt
Saving ENG.G0.49.3.txt to ENG.G0.4

In [3]:
type(uploaded_files)

dict

In [4]:
paper_df = pd.DataFrame.from_dict(uploaded_files, orient='index')
paper_df.head()

0
ENG.G0.35.1.txt  b" A play with a plot based on various complic...
ENG.G0.35.2.txt  b" \tLove has been the topic of literature for...
ENG.G0.36.1.txt  b" \tAs he walks along Sandymount Strand in th...
ENG.G0.37.1.txt  b'\nPersonal interpretations of past time\xe2\...
ENG.G0.38.1.txt  b" Unlike many other versions of this famous S...

In [5]:
#from pickle import TRUE      #JD -- who is pickle lol
# Reset index and add column names to make wrangling easier
paper_df = paper_df.reset_index()
paper_df.columns = ["Filename", "Text"]

In [ ]:
#paper_df = pd.DataFrame.from_dict(uploaded_files, orient='index')
#paper_df.head() #Recheck, causes some minor issues, do not run!!!

0
BIO.G0.01.1 (2).txt  b"Introduction\xe2\x80\xa6\xe2\x80\xa6\xe2\x80...
BIO.G0.02.1 (2).txt  b'      Ernst Mayr once wrote, sympatric speci...
BIO.G0.02.2 (2).txt  b"      Do ecological constraints favour certa...
BIO.G0.02.3 (2).txt  b"       Perhaps one of the most intriguing va...
BIO.G0.02.4 (2).txt  b"      The causal link between chromosomal re...

In [ ]:
paper_df.rename(columns={'index':'Filename', 0: 'Text'}) #Inferred from previous class, code, odd that the actual assignment does not include this

Filename                                               Text
0    BIO.G0.01.1.txt  b"Introduction\xe2\x80\xa6\xe2\x80\xa6\xe2\x80...
1    BIO.G0.02.1.txt  b'      Ernst Mayr once wrote, sympatric speci...
2    BIO.G0.02.2.txt  b"      Do ecological constraints favour certa...
3    BIO.G0.02.3.txt  b"       Perhaps one of the most intriguing va...
4    BIO.G0.02.4.txt  b"      The causal link between chromosomal re...
..               ...                                                ...
160  ENG.G2.05.1.txt  b' \xef\xbb\xbfFor more than 1600 years a Chur...
161  ENG.G2.06.1.txt  b'\nI had become [a slave to Stieglitz\xe2\x80...
162  ENG.G2.07.1.txt  b'       The pedagogical materials we use in o...
163  ENG.G3.03.1.txt  b"\nIt is necessary, while in darkness, to kno...
164  ENG.G3.04.1.txt  b'       In her essay Nuance and the Novella, ...

[165 rows x 2 columns]

In [6]:
paper_df['Text'] = paper_df['Text'].str.decode('utf-8')
paper_df.head()

Filename                                               Text
0  ENG.G0.35.1.txt   A play with a plot based on various complicat...
1  ENG.G0.35.2.txt   \tLove has been the topic of literature for c...
2  ENG.G0.36.1.txt   \tAs he walks along Sandymount Strand in the ...
3  ENG.G0.37.1.txt  \nPersonal interpretations of past time—the st...
4  ENG.G0.38.1.txt   Unlike many other versions of this famous Sha...

In [7]:
paper_df['Text'] = paper_df['Text'].str.replace('\s+', ' ', regex=True).str.strip()

In [8]:
metadata = files.upload()

Saving metadata.csv to metadata.csv


In [9]:
metadata_df = pd.read_csv('metadata.csv')
metadata_df = metadata_df.dropna(axis=1, how='all')
#metadata_df #added for testing purposes

In [10]:
# Remove .txt from title of each paper
paper_df['Filename'] = paper_df['Filename'].str.replace('.txt', '')

# Rename column from paper ID to Title
metadata_df.rename(columns={"PAPER ID": "Filename"}, inplace=True)

<ipython-input-10-2069ef833468>:2: FutureWarning: The default value of regex will change from True to False in a future version.
  paper_df['Filename'] = paper_df['Filename'].str.replace('.txt', '')


In [11]:
paper_df['Filename'] = paper_df['Filename'].str.strip()
metadata_df['Filename'] = metadata_df['Filename'].str.strip()

In [ ]:
#paper_df.set_index('Filename') Attempted Debugging, not work
#metadata_df.set_index('Filename')

In [12]:
final_paper_df = metadata_df.merge(paper_df,on='Filename') #suffixes=False,False)
final_paper_df #WHERE ARE THE ENTRIES????????


Filename                                              TITLE  \
0    BIO.G0.15.1  Invading the Territory of Invasives: The Dange...   
1    BIO.G1.04.1  The Evolution of Terrestriality: A Look at the...   
2    BIO.G3.03.1  Intracellular Electric Field Sensing using Nan...   
3    BIO.G0.11.1  Exploring the Molecular Responses of Arabidops...   
4    BIO.G1.01.1  V. Cholerae: First Steps towards a Spatially E...   
..           ...                                                ...   
160  ENG.G1.07.1                          Categorical Entanglement    
161  ENG.G2.06.1                        Jews in the New York Harbor   
162  ENG.G2.07.1                                 Pedagogical genres   
163  ENG.G0.38.1                           Roman Polanski's Macbeth   
164  ENG.G0.38.2                               Julie Taymor's Titus   

    DISCIPLINE           PAPER TYPE  \
0      Biology  Argumentative Essay   
1      Biology  Argumentative Essay   
2      Biology  Argumentative Essay   
3      Biology             Proposal   
4      Biology             Proposal   
..         ...                  ...   
160    English               Report   
161    English               Report   
162    English               Report   
163    English       Response Paper   
164    English       Response Paper   

                                                  Text  
0    New York City, 1908: different colors of skin ...  
1    The fish-tetrapod transition has been called t...  
2    Intracellular electric fields are of great int...  
3    Environmental stresses to plants have been stu...  
4    The recurrent cholera pandemics have been rela...  
..                                                 ...  
160  ﻿ Trauma, from the Greek for wound originally ...  
161  I had become [a slave to Stieglitz’s eye] from...  
162  The pedagogical materials we use in our compos...  
163  Unlike many other versions of this famous Shak...  
164  Modern cinema possesses the ability to present...  

[165 rows x 5 columns]

In [13]:
final_paper_df.sample(30) #WHERE ARE THE ENTRIES????????

Filename                                              TITLE  \
151  ENG.G0.33.1  Limited Recovery: Trauma in Obejas' Cuban America   
158  ENG.G0.54.1     Analysis of T.C. Boyle's A Friend of the Earth   
14   BIO.G0.04.1                             Fetal Endocrine System   
5    BIO.G1.07.1                    Zebrafish and PGC mis-migration   
156  ENG.G0.43.2                               Defining Wild Nature   
134  ENG.G0.38.3                                    Return to Suomi   
136  ENG.G0.30.1    SIgnificance of Menstruation in Joyce's Ulysses   
68   ENG.G0.03.1                                   HIV-AIDS Funding   
40   BIO.G0.03.1                           Lab 3: Plant Competition   
12   BIO.G0.02.4  Chromosomal Rearrangements, Recombination Supp...   
47   BIO.G0.08.1          Analysis of a Mutant Strain of Drosophila   
65   BIO.G0.31.1       Neurobiology Disease Explanation to a Parent   
82   ENG.G0.18.1       Individuality and Isolation in Moll Flanders   
93   ENG.G0.26.2  Comparison of Hermia in A Midsummer Night's Dr...   
119  ENG.G0.55.2                        Illustrations in Persepolis   
123  ENG.G1.04.1              Sports Literacy and Rhetoric as Power   
143  ENG.G0.10.1     Close Reading Paper: The Tempest (4.1.146-163)   
42   BIO.G0.03.3  Comparison of Hypothesis Testing in a High vs....   
131  ENG.G3.04.1  Creative Multivalence: Social Engagement in Gw...   
76   ENG.G0.11.1    Bloom & Martha: Are You Not Happy in Your Home?   
32   BIO.G1.03.1                  Dispersal: a Review and Synthesis   
29   BIO.G0.29.1  Sexual Selection and Male Sacrifice:  From Dar...   
37   BIO.G2.05.2       Assignment: Subcellular Protein Localization   
87   ENG.G0.20.1                        Autonomy in Robinson Crusoe   
21   BIO.G0.13.1                   Malaria Disease and Transmission   
44   BIO.G0.04.3                             Conjugation Lab Report   
127  ENG.G2.02.1  Dramatic Adaptations: Jewish Identity and Narr...   
20   BIO.G0.12.2                  Lab Report 2: Plant Biodiversity    
92   ENG.G0.25.1  Sexualized Violence and Identity in Achy Obeja...   
116  ENG.G0.52.1              Deborah and the Degradation of Israel   

    DISCIPLINE           PAPER TYPE  \
151    English               Report   
158    English               Report   
14     Biology               Report   
5      Biology             Proposal   
156    English               Report   
134    English     Creative Writing   
136    English  Critique/Evaluation   
68     English  Argumentative Essay   
40     Biology       Research Paper   
12     Biology               Report   
47     Biology       Research Paper   
65     Biology       Response Paper   
82     English  Argumentative Essay   
93     English  Argumentative Essay   
119    English  Argumentative Essay   
123    English  Argumentative Essay   
143    English               Report   
42     Biology       Research Paper   
131    English  Argumentative Essay   
76     English  Argumentative Essay   
32     Biology               Report   
29     Biology               Report   
37     Biology               Report   
87     English  Argumentative Essay   
21     Biology               Report   
44     Biology       Research Paper   
127    English  Argumentative Essay   
20     Biology               Report   
92     English  Argumentative Essay   
116    English  Argumentative Essay   

                                                  Text  
151  I have done that, says my memory. I cannot hav...  
158  ﻿A Friend of the Earth, T.C. Boyle’s satirical...  
14   This article reviews the effects that maternal...  
5    There are two interesting phenomena in this re...  
156  Defining wildness – even tracing another’s def...  
134  The must of the old farmhouse seared my nostri...  
136  Throughout James Joyce's Ulysses, the protagon...  
68   At the end of 2006, over 39.5 million people w...  
40   The ability of a species to compete for limite...  
12   The causal link betwe

In [14]:
paper_df

Filename                                               Text
0    ENG.G0.35.1  A play with a plot based on various complicati...
1    ENG.G0.35.2  Love has been the topic of literature for cent...
2    ENG.G0.36.1  As he walks along Sandymount Strand in the Pro...
3    ENG.G0.37.1  Personal interpretations of past time—the stor...
4    ENG.G0.38.1  Unlike many other versions of this famous Shak...
..           ...                                                ...
160  ENG.G0.32.1  Slavery has long been both the subject of writ...
161  ENG.G0.33.1  I have done that, says my memory. I cannot hav...
162  ENG.G0.34.1  In the Gospel of Mark, Jesus redefines the fam...
163  ENG.G0.34.2  The book of Hosea reaffirms the first word of ...
164  ENG.G0.34.3  The authors of Genesis 1 and 2, whoever they m...

[165 rows x 2 columns]

In [15]:
metadata_df

Filename                                              TITLE  \
0    BIO.G0.15.1  Invading the Territory of Invasives: The Dange...   
1    BIO.G1.04.1  The Evolution of Terrestriality: A Look at the...   
2    BIO.G3.03.1  Intracellular Electric Field Sensing using Nan...   
3    BIO.G0.11.1  Exploring the Molecular Responses of Arabidops...   
4    BIO.G1.01.1  V. Cholerae: First Steps towards a Spatially E...   
..           ...                                                ...   
160  ENG.G1.07.1                          Categorical Entanglement    
161  ENG.G2.06.1                        Jews in the New York Harbor   
162  ENG.G2.07.1                                 Pedagogical genres   
163  ENG.G0.38.1                           Roman Polanski's Macbeth   
164  ENG.G0.38.2                               Julie Taymor's Titus   

    DISCIPLINE           PAPER TYPE  
0      Biology  Argumentative Essay  
1      Biology  Argumentative Essay  
2      Biology  Argumentative Essay  
3      Biology             Proposal  
4      Biology             Proposal  
..         ...                  ...  
160    English               Report  
161    English               Report  
162    English               Report  
163    English       Response Paper  
164    English       Response Paper  

[165 rows x 4 columns]

In [16]:
nlp = spacy.load('en_core_web_sm')

print(nlp.pipe_names)

['tok2vec', 'tagger', 'parser', 'attribute_ruler', 'lemmatizer', 'ner']


In [17]:
sentence = "This is 'an' example? sentence"

doc = nlp(sentence)

In [18]:
for token in doc:
    print(token.text, token.pos_)

This PRON
is AUX
' PUNCT
an DET
' PUNCT
example NOUN
? PUNCT
sentence NOUN


In [19]:
def process_text(text):
    return nlp(text)

In [20]:
final_paper_df['Doc'] = final_paper_df['Text'].apply(process_text)

In [21]:
def get_token(doc):
    for token in doc:
        return token.text

In [22]:
def get_token(doc):
    return [(token.text) for token in doc]

In [23]:
final_paper_df['Tokens'] = final_paper_df['Doc'].apply(get_token)

In [24]:
final_paper_df

Filename                                              TITLE  \
0    BIO.G0.15.1  Invading the Territory of Invasives: The Dange...   
1    BIO.G1.04.1  The Evolution of Terrestriality: A Look at the...   
2    BIO.G3.03.1  Intracellular Electric Field Sensing using Nan...   
3    BIO.G0.11.1  Exploring the Molecular Responses of Arabidops...   
4    BIO.G1.01.1  V. Cholerae: First Steps towards a Spatially E...   
..           ...                                                ...   
160  ENG.G1.07.1                          Categorical Entanglement    
161  ENG.G2.06.1                        Jews in the New York Harbor   
162  ENG.G2.07.1                                 Pedagogical genres   
163  ENG.G0.38.1                           Roman Polanski's Macbeth   
164  ENG.G0.38.2                               Julie Taymor's Titus   

    DISCIPLINE           PAPER TYPE  \
0      Biology  Argumentative Essay   
1      Biology  Argumentative Essay   
2      Biology  Argumentative Essay   
3      Biology             Proposal   
4      Biology             Proposal   
..         ...                  ...   
160    English               Report   
161    English               Report   
162    English               Report   
163    English       Response Paper   
164    English       Response Paper   

                                                  Text  \
0    New York City, 1908: different colors of skin ...   
1    The fish-tetrapod transition has been called t...   
2    Intracellular electric fields are of great int...   
3    Environmental stresses to plants have been stu...   
4    The recurrent cholera pandemics have been rela...   
..                                                 ...   
160  ﻿ Trauma, from the Greek for wound originally ...   
161  I had become [a slave to Stieglitz’s eye] from...   
162  The pedagogical materials we use in our compos...   
163  Unlike many other versions of this famous Shak...   
164  Modern cinema possesses the ability to present...   

                                                   Doc  \
0    (New, York, City, ,, 1908, :, different, color...   
1    (The, fish, -, tetrapod, transition, has, been...   
2    (Intracellular, electric, fields, are, of, gre...   
3    (Environmental, stresses, to, plants, have, be...   
4    (The, recurrent, cholera, pandemics, have, bee...   
..                                                 ...   
160  (﻿, Trauma, ,, from, the, Greek, for, wound, o...   
161  (I, had, become, [, a, slave, to, Stieglitz, ’...   
162  (The, pedagogical, materials, we, use, in, our...   
163  (Unlike, many, other, versions, of, this, famo...   
164  (Modern, cinema, possesses, the, ability, to, ...   

                                                Tokens  
0    [New, York, City, ,, 1908, :, different, color...  
1    [The, fish, -, tetrapod, transition, has, been...  
2    [Intracellular, electric, fields, are, of, gre...  
3    [Environmental, stresses, to, plants, have, be...  
4    [The, recurrent, cholera, pandemics, have, bee...  
..                                                 ...  
160  [﻿, Trauma, ,, from, the, Greek, for, wound, o...  
161  [I, had, become, [, a, slave, to, Stieglitz, ’...  
162  [The, pedagogical, materials, we, use, in, our...  
163  [Unlike, many, other, versions, of, this, famo...  
164  [Modern, cinema, possesses, the, ability, to, ...  

[165 rows x 7 columns]

In [25]:
def get_lemma(doc):
    return [(token.lemma_) for token in doc]

final_paper_df['Lemmas'] = final_paper_df['Doc'].apply(get_lemma)

In [26]:
print(f'"Write" appears in the text tokens column ' + str(final_paper_df['Tokens'].apply(lambda x: x.count('write')).sum()) + ' times.')
print(f'"Write" appears in the lemmas column ' + str(final_paper_df['Lemmas'].apply(lambda x: x.count('write')).sum()) + ' times.')

"Write" appears in the text tokens column 40 times.
"Write" appears in the lemmas column 310 times.


In [27]:
def get_pos(doc):
    return [(token.pos_, token.tag_) for token in doc]

final_paper_df['POS'] = final_paper_df['Doc'].apply(get_pos)

In [28]:
list(final_paper_df['POS'])

[[('PROPN', 'NNP'),
  ('PROPN', 'NNP'),
  ('PROPN', 'NNP'),
  ('PUNCT', ','),
  ('NUM', 'CD'),
  ('PUNCT', ':'),
  ('ADJ', 'JJ'),
  ('NOUN', 'NNS'),
  ('ADP', 'IN'),
  ('NOUN', 'NN'),
  ('NOUN', 'NN'),
  ('ADP', 'IN'),
  ('DET', 'DT'),
  ('ADJ', 'JJ'),
  ('NOUN', 'NN'),
  ('NOUN', 'NN'),
  ('PART', 'TO'),
  ('VERB', 'VB'),
  ('DET', 'DT'),
  ('ADJ', 'JJ'),
  ('NOUN', 'NN'),
  ('PUNCT', '.'),
  ('ADV', 'RB'),
  ('VERB', 'VB'),
  ('DET', 'PDT'),
  ('DET', 'DT'),
  ('NOUN', 'NN'),
  ('VERB', 'VBG'),
  ('PART', 'TO'),
  ('VERB', 'VB'),
  ('DET', 'DT'),
  ('ADJ', 'JJ'),
  ('NOUN', 'NN'),
  ('ADP', 'IN'),
  ('PROPN', 'NNP'),
  ('PUNCT', '.'),
  ('ADP', 'IN'),
  ('NOUN', 'NN'),
  ('PUNCT', ','),
  ('NOUN', 'NNS'),
  ('AUX', 'MD'),
  ('VERB', 'VB'),
  ('PART', 'TO'),
  ('VERB', 'VB'),
  ('DET', 'DT'),
  ('ADJ', 'JJ'),
  ('NOUN', 'NN'),
  ('PUNCT', ':'),
  ('SCONJ', 'IN'),
  ('ADJ', 'JJ'),
  ('NOUN', 'NNS'),
  ('AUX', 'MD'),
  ('AUX', 'VB'),
  ('VERB', 'VBN'),
  ('PUNCT', '.'),
  ('PRON', 'PRP$

In [29]:
def extract_proper_nouns(doc):
    return [token.text for token in doc if token.pos_ == 'PROPN']

final_paper_df['Proper_Nouns'] = final_paper_df['Doc'].apply(extract_proper_nouns)

In [30]:
list(final_paper_df.loc[[3, 163], 'Proper_Nouns'])

[['Mars',
  'Arabidopsis',
  'Arabidopsis',
  'LEA',
  'COR',
  'LEA',
  'NASA',
  'MIPs',
  'MIPs',
  'MIPs',
  'Earth',
  'Arabidopsis',
  'Arabidopsis',
  'Pressure',
  'Growth',
  'Chamber',
  'LPGC',
  'Paul',
  'et',
  'al',
  '.',
  'Musgrave',
  'et',
  'al',
  'Mars',
  'LPGC',
  'mmol',
  'L.',
  'Musgrave',
  'et',
  'al',
  'CO2',
  'O2',
  'Earth',
  'GeneChip',
  'Arabidopsis',
  'Paul',
  'et',
  'al',
  '.',
  'mRNA',
  'RNA',
  'RNA',
  'Paul',
  'et',
  'al',
  '.',
  'experiment',
  'Paul',
  'et',
  'al',
  '.',
  'experiment',
  'ADH',
  'ADH',
  'Arabidopsis',
  'RT',
  'PCR',
  'C4',
  'RT',
  'PCR',
  'Paul',
  'et',
  'al',
  'mRNA',
  'LEA',
  'ABIs',
  'Heat',
  'Shock',
  'Proteins',
  'mRNA',
  'Microarrays',
  'RT',
  'PCR',
  'Expression',
  'Analysis',
  'Systematic',
  'Explorer',
  'Liu',
  'et',
  'al',
  'LPGC',
  'LEA',
  'COR',
  'LEA',
  'COR',
  'ABA',
  'ABA',
  'CBFs',
  'DRE',
  'DRE',
  'mRNA',
  'Silencer',
  'RNA',
  'ABA',
  'CBF3',
  'COR

In [31]:
doc = final_paper_df['Doc'][5]
sentences = list(doc.sents)
sentence = sentences[1]
displacy.render(sentence, style="dep", jupyter=True)

In [32]:
def extract_stopwords(doc):
    return [token.text for token in doc if token.text not in nlp.Defaults.stop_words]

final_paper_df['Tokens_NoStops'] = final_paper_df['Doc'].apply(extract_stopwords)

final_paper_df['Text_NoStops'] = [' '.join(map(str, l)) for l in final_paper_df['Tokens_NoStops']]

final_paper_df['Doc_NoStops'] = final_paper_df['Text_NoStops'].apply(process_text)

doc = final_paper_df['Doc_NoStops'][5]
sentences = list(doc.sents)
sentence = sentences[0]

displacy.render(sentence, style='dep', jupyter=True)

In [33]:
def extract_noun_phrases(doc):
    return [chunk.text for chunk in doc.noun_chunks]

final_paper_df['Noun_Phrases'] = final_paper_df['Doc'].apply(extract_noun_phrases)

In [34]:
labels = nlp.get_pipe("ner").labels

for label in labels:
    print(label + ' : ' + spacy.explain(label))

CARDINAL : Numerals that do not fall under another type
DATE : Absolute or relative dates or periods
EVENT : Named hurricanes, battles, wars, sports events, etc.
FAC : Buildings, airports, highways, bridges, etc.
GPE : Countries, cities, states
LANGUAGE : Any named language
LAW : Named documents made into laws.
LOC : Non-GPE locations, mountain ranges, bodies of water
MONEY : Monetary values, including unit
NORP : Nationalities or religious or political groups
ORDINAL : "first", "second", etc.
ORG : Companies, agencies, institutions, etc.
PERCENT : Percentage, including "%"
PERSON : People, including fictional
PRODUCT : Objects, vehicles, foods, etc. (not services)
QUANTITY : Measurements, as of weight or distance
TIME : Times smaller than a day
WORK_OF_ART : Titles of books, songs, etc.


In [35]:
def extract_named_entities(doc):
    return [ent.label_ for ent in doc.ents]

final_paper_df['Named_Entities'] = final_paper_df['Doc'].apply(extract_named_entities)
final_paper_df['Named_Entities']

0      [GPE, DATE, LOC, PERSON, GPE, DATE, PERSON, GP...
1      [PERSON, PERSON, DATE, ORG, DATE, PERSON, DATE...
2      [PERCENT, CARDINAL, DATE, CARDINAL, ORDINAL, O...
3      [LOC, FAC, GPE, ORDINAL, ORG, ORG, ORG, CARDIN...
4      [ORDINAL, ORG, ORG, DATE, LOC, GPE, ORDINAL, D...
                             ...                        
160    [PERSON, NORP, DATE, EVENT, CARDINAL, EVENT, P...
161    [ORG, ORG, ORG, GPE, GPE, PERSON, GPE, NORP, N...
162    [PRODUCT, PERSON, PERSON, ORG, PERSON, CARDINA...
163    [PERSON, PERSON, PERSON, PERSON, ORG, PERSON, ...
164    [PERSON, ORG, PERSON, PRODUCT, PERSON, PERSON,...
Name: Named_Entities, Length: 165, dtype: object

In [36]:
def extract_named_entities(doc):
    return [ent for ent in doc.ents]

final_paper_df['NE_Words'] = final_paper_df['Doc'].apply(extract_named_entities)
final_paper_df['NE_Words']

0      [(New, York, City), (1908), (Earth), (Mooney),...
1      [(Long), (Gordon), (2004), (Carroll), (2001), ...
2      [(less, than, .1, %), (only, one), (1250V), (1...
3      [(Mars), (Arabidopsis, thaliana), (Arabidopsis...
4      [(first), (Point, Pattern, Analysis), (Geostat...
                             ...                        
160    [(﻿, Trauma), (Greek), (Today), (Vietnam, War)...
161    [(Stieglitz), (Steerage), (Stieglitz), (New, Y...
162    [(Paré), (Miller), (Paré), (Myers), (Nancy, My...
163    [(Roman, Polanski), (MacBeth), (MacBeth), (Pol...
164    [(Shakespeare), (Bard), (Julie, Taymor, 's), (...
Name: NE_Words, Length: 165, dtype: object

In [37]:
doc = final_paper_df['Doc'][1]
displacy.render(doc, style='ent', jupyter=True)

In [38]:
# Save DataFrame as csv (in Google Drive)
final_paper_df.to_csv('MICUSP_papers_with_spaCy_tags.csv')

# Download csv to your computer from Google Drive
files.download('MICUSP_papers_with_spaCy_tags.csv')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [39]:
# Create Doc object from single sentence
doc = nlp("This is 'an' example? sentence")

# Print counts of each part of speech in sentence
print(doc.count_by(spacy.attrs.POS))

{95: 1, 87: 1, 97: 3, 90: 1, 92: 2}


In [40]:
num_list = []

# Create new DataFrame for analysis purposes
pos_analysis_df = final_paper_df[['Filename','DISCIPLINE', 'Doc']]

def get_pos_tags(doc):
    dictionary = {}
    num_pos = doc.count_by(spacy.attrs.POS)
    for k,v in sorted(num_pos.items()):
        dictionary[doc.vocab[k].text] = v
    num_list.append(dictionary)

pos_analysis_df['C_POS'] = pos_analysis_df['Doc'].apply(get_pos_tags)

<ipython-input-40-635e26f60dda>:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pos_analysis_df['C_POS'] = pos_analysis_df['Doc'].apply(get_pos_tags)


In [41]:
pos_counts = pd.DataFrame(num_list)
columns = list(pos_counts.columns)
idx = 0
new_col = pos_analysis_df['DISCIPLINE']
pos_counts.insert(loc=idx, column='DISCIPLINE', value=new_col)
pos_counts.head()

DISCIPLINE  ADJ  ADP  ADV  AUX  CCONJ  DET  INTJ  NOUN  NUM  PART  PRON  \
0    Biology  180  174   62  106     42  137     1   342   29    29    41   
1    Biology  421  458  174  253    187  389     1   868  193    78   121   
2    Biology  163  171   63   91     51  148     1   362    6    31    23   
3    Biology  318  402  120  267    121  317     1   908  101    93   128   
4    Biology  294  388   97  142     97  299     1   734   89    41    36   

   PROPN  PUNCT  SCONJ  VERB  SYM    X  
0    101    196     16   139  NaN  NaN  
1    379    786     99   389  1.0  2.0  
2     44    134     15   114  4.0  1.0  
3    151    487     92   387  4.0  NaN  
4    246    465     36   233  1.0  7.0

In [42]:
average_pos_df = pos_counts.groupby(['DISCIPLINE']).mean()

average_pos_df = average_pos_df.round(0)

average_pos_df = average_pos_df.reset_index()

average_pos_df

DISCIPLINE    ADJ    ADP    ADV    AUX  CCONJ    DET  INTJ   NOUN   NUM  \
0    Biology  237.0  299.0   93.0  141.0   89.0  234.0   1.0  614.0  81.0   
1    English  211.0  364.0  127.0  141.0  108.0  283.0   2.0  578.0  34.0   

   PART   PRON  PROPN  PUNCT  SCONJ   VERB  SYM    X  
0  44.0   74.0  194.0  343.0   50.0  237.0  8.0  6.0  
1  99.0  223.0  189.0  367.0   70.0  306.0  7.0  5.0

G-Note: The Next Two Cells Do Not Work --

1) Average_Tag Def Has Not Been Defined

2) tag_counts has not been defined

It doesn't break later cells, but it is annoying

In [43]:
tag_num_list = []
def get_fine_pos_tags(doc):
    dictionary = {}
    num_tag = doc.count_by(spacy.attrs.TAG)
    for k,v in sorted(num_tag.items()):
        dictionary[doc.vocab[k].text] = v
    tag_num_list.append(dictionary)

pos_analysis_df['F_POS'] = pos_analysis_df['Doc'].apply(get_fine_pos_tags)


<ipython-input-43-0a70b108704e>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pos_analysis_df['F_POS'] = pos_analysis_df['Doc'].apply(get_fine_pos_tags)


In [44]:
average_tag_df = average_pos_df.groupby(['DISCIPLINE']).mean()

average_tag_df = average_tag_df.round(0)

average_tag_df = average_tag_df.reset_index()

average_tag_df

DISCIPLINE    ADJ    ADP    ADV    AUX  CCONJ    DET  INTJ   NOUN   NUM  \
0    Biology  237.0  299.0   93.0  141.0   89.0  234.0   1.0  614.0  81.0   
1    English  211.0  364.0  127.0  141.0  108.0  283.0   2.0  578.0  34.0   

   PART   PRON  PROPN  PUNCT  SCONJ   VERB  SYM    X  
0  44.0   74.0  194.0  343.0   50.0  237.0  8.0  6.0  
1  99.0  223.0  189.0  367.0   70.0  306.0  7.0  5.0

In [ ]:
ner_analysis_df = final_paper_df[['Filename','PAPER TYPE', 'Named_Entities', 'NE_Words']]

In [ ]:
ner_analysis_df['Named_Entities'] = ner_analysis_df['Named_Entities'].apply(lambda x: ' '.join(x))

person_counts = ner_analysis_df['Named_Entities'].str.count('PERSON')
org_counts = ner_analysis_df['Named_Entities'].str.count('ORG')
date_counts = ner_analysis_df['Named_Entities'].str.count('DATE')
woa_counts = ner_analysis_df['Named_Entities'].str.count('WORK_OF_ART')

ner_counts_df = pd.DataFrame()
ner_counts_df['Genre'] = ner_analysis_df["PAPER TYPE"]
ner_counts_df['PERSON_Counts'] = person_counts
ner_counts_df['ORG_Counts'] = org_counts
ner_counts_df['DATE_Counts'] = date_counts
ner_counts_df['WORK_OF_ART_Counts'] = woa_counts

<ipython-input-52-d9f8116fb63e>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ner_analysis_df['Named_Entities'] = ner_analysis_df['Named_Entities'].apply(lambda x: ' '.join(x))


In [ ]:
def extract_date_named_entities(doc):
    return [ent for ent in doc.ents if ent.label_ == 'DATE']

ner_analysis_df['Date_Named_Entities'] = final_paper_df['Doc'].apply(extract_date_named_entities)

ner_analysis_df['Date_Named_Entities'] = [', '.join(map(str, l)) for l in ner_analysis_df['Date_Named_Entities']]

<ipython-input-53-25fd1f0e9f06>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ner_analysis_df['Date_Named_Entities'] = final_paper_df['Doc'].apply(extract_date_named_entities)
<ipython-input-53-25fd1f0e9f06>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ner_analysis_df['Date_Named_Entities'] = [', '.join(map(str, l)) for l in ner_analysis_df['Date_Named_Entities']]


In [ ]:
date_word_counts_df = ner_analysis_df[(ner_analysis_df == 'Proposal').any(axis=1)]

date_word_frequencies = date_word_counts_df.Date_Named_Entities.str.split(expand=True).stack().value_counts()
date_word_frequencies[:10]


2004,      24
2003,      18
the        17
2002,      12
2005,      11
1998,      11
2000,       9
year,       9
1977,       8
season,     8
dtype: int64

In [ ]:
# Search for only date words in critique/evaluation papers
date_word_counts_df = ner_analysis_df[(ner_analysis_df == 'Critique/Evaluation').any(axis=1)]

# Count the frequency of each word in these papers and append to list
date_word_frequencies = date_word_counts_df.Date_Named_Entities.str.split(expand=True).stack().value_counts()

# Get top 10 most common words and their frequencies
date_word_frequencies[:10]

the         10
winter,      8
years,       6
2009         5
1950,        5
1960,        5
century,     4
decade,      3
of           3
decades,     3
dtype: int64